In [52]:
import pandas as pd
import numpy as np
import re
import warnings
warnings.filterwarnings("ignore")

import nltk
from textblob import TextBlob

In [68]:
pip install wordcloud

  Obtaining dependency information for wordcloud from https://files.pythonhosted.org/packages/f5/b0/247159f61c5d5d6647171bef84430b7efad4db504f0229674024f3a4f7f2/wordcloud-1.9.3-cp311-cp311-win_amd64.whl.metadata
   ---------------------------------------- 0.0/300.2 kB ? eta -:--:--
   - -------------------------------------- 10.2/300.2 kB ? eta -:--:--
   --- ----------------------------------- 30.7/300.2 kB 435.7 kB/s eta 0:00:01
   --------------------- ------------------ 163.8/300.2 kB 1.4 MB/s eta 0:00:01
   ---------------------------------------  297.0/300.2 kB 2.3 MB/s eta 0:00:01
   ---------------------------------------- 300.2/300.2 kB 1.9 MB/s eta 0:00:00
Note: you may need to restart the kernel to use updated packages.


In [69]:
import gensim
from gensim import corpora
from gensim.utils import simple_preprocess

import pyLDAvis
import pyLDAvis.gensim_models as gensimvis
from wordcloud import WordCloud, STOPWORDS
import seaborn as sns
import matplotlib.pyplot as plt

Matplotlib is building the font cache; this may take a moment.


In [31]:
df1=pd.read_csv('netflix_reviews.csv')

In [32]:
df1.head()

reviewId         userName  \
0  8e34c46f-600a-49db-aa99-5ebc64c0513c    Adrian Delrio   
1  011d817a-c12b-48e7-a686-d5a7b16193e2    charif haidar   
2  07c4146a-0c30-4c6c-b8ac-5194b0fdaf92  Kaycee Kingsley   
3  38da9275-be72-403b-b2f4-d998656fd4e8     Shaik Tabrez   
4  926cb80a-f22d-49d2-87b3-8d81736c2102  Maurisha Harris   

                                             content  score  thumbsUpCount  \
0                        I can watch a lot of movies      5              0   
1  They make you pay for a membership then they t...      1              0   
2                                               Good      5              0   
3  I really enjoy Netflix. But why is Netflix con...      3              0   
4                     The app doesn't want to update      1              0   

    reviewCreatedVersion                   at             appVersion  
0  8.116.0 build 8 50690  2024-05-29 21:55:09  8.116.0 build 8 50690  
1  8.116.0 build 8 50690  2024-05-29 21:54:40  8.116.0 build 8 50690  
2   8.28.0 build 4 40234  2024-05-29 21:38:20   8.28.0 build 4 40234  
3  8.116.0 build 8 50690  2024-05-29 21:18:29  8.116.0 build 8 50690  
4  8.116.0 build 8 50690  2024-05-29 21:03:10  8.116.0 build 8 50690

In [33]:
df1.columns

Index(['reviewId', 'userName', 'content', 'score', 'thumbsUpCount',
       'reviewCreatedVersion', 'at', 'appVersion'],
      dtype='object')

In [34]:
df1.shape

(111155, 8)

In [35]:
df1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 111155 entries, 0 to 111154
Data columns (total 8 columns):
 #   Column                Non-Null Count   Dtype 
---  ------                --------------   ----- 
 0   reviewId              111155 non-null  object
 1   userName              111154 non-null  object
 2   content               111153 non-null  object
 3   score                 111155 non-null  int64 
 4   thumbsUpCount         111155 non-null  int64 
 5   reviewCreatedVersion  95156 non-null   object
 6   at                    111155 non-null  object
 7   appVersion            95156 non-null   object
dtypes: int64(2), object(6)
memory usage: 6.8+ MB


In [8]:
df=df[['reviewId','userName','content','score']]
df

reviewId         userName  \
0       8e34c46f-600a-49db-aa99-5ebc64c0513c    Adrian Delrio   
1       011d817a-c12b-48e7-a686-d5a7b16193e2    charif haidar   
2       07c4146a-0c30-4c6c-b8ac-5194b0fdaf92  Kaycee Kingsley   
3       38da9275-be72-403b-b2f4-d998656fd4e8     Shaik Tabrez   
4       926cb80a-f22d-49d2-87b3-8d81736c2102  Maurisha Harris   
...                                      ...              ...   
111150  a760ead9-e7aa-4ed1-a651-5c37c3600dac    A Google user   
111151  4957f9e7-d7f4-4a52-9764-031cebcac83f     Captain Jeoy   
111152  9acf7586-7abf-4b50-8c50-3ede3b2a42c4         Suryansh   
111153  32870f7f-c461-4256-b602-75244ca60248    A Google user   
111154  dc1352e9-10a8-41ca-ab23-05d045b08e90       suraj soni   

                                                  content  score  
0                             I can watch a lot of movies      5  
1       They make you pay for a membership then they t...      1  
2                                                    Good      5  
3       I really enjoy Netflix. But why is Netflix con...      3  
4                          The app doesn't want to update      1  
...                                                   ...    ...  
111150  i really like it! there are so many movies and...      5  
111151   I love Netflix. I always enjoy my time using it.      5  
111152               Sound quality is very slow of movies      1  
111153  Rate is very expensive.. bcos we see netflix s...      1  
111154  this app is awesome for english movies ,series...      4  

[111155 rows x 4 columns]

In [36]:
def preprocess_text(text):
    if isinstance(text, float):
        return ""
    text = text.lower()  
    text = re.sub(r'[^\w\s]', '', text)  
    text = re.sub(r'\d+', '', text) 
    text = text.strip()  
    return text

In [37]:
df1['content_c']=df1['content'].apply(preprocess_text)

In [38]:
df1['content'][1]

'They make you pay for a membership then they tell you you cannot stream video on TV until you pay more, what a scam!'

In [39]:
df1['content_c'][1]

'they make you pay for a membership then they tell you you cannot stream video on tv until you pay more what a scam'

In [40]:
df1.isnull().sum().sum()

32001

In [41]:
df1.fillna('', inplace=True)

In [42]:
df1.columns

Index(['reviewId', 'userName', 'content', 'score', 'thumbsUpCount',
       'reviewCreatedVersion', 'at', 'appVersion', 'content_c'],
      dtype='object')

In [44]:
df1['at'] = pd.to_datetime(df1['at'])

In [47]:
df2 = df1[['content_c', 'score', 'reviewId', 'at']]
df2.head()

content_c  score  \
0                        i can watch a lot of movies      5   
1  they make you pay for a membership then they t...      1   
2                                               good      5   
3  i really enjoy netflix but why is netflix conf...      3   
4                      the app doesnt want to update      1   

                               reviewId                  at  
0  8e34c46f-600a-49db-aa99-5ebc64c0513c 2024-05-29 21:55:09  
1  011d817a-c12b-48e7-a686-d5a7b16193e2 2024-05-29 21:54:40  
2  07c4146a-0c30-4c6c-b8ac-5194b0fdaf92 2024-05-29 21:38:20  
3  38da9275-be72-403b-b2f4-d998656fd4e8 2024-05-29 21:18:29  
4  926cb80a-f22d-49d2-87b3-8d81736c2102 2024-05-29 21:03:10

In [49]:
print("Earliest review date:", df2['at'].min())
print("Latest review date:", df2['at'].max())

Earliest review date: 2018-09-12 07:22:12
Latest review date: 2024-05-29 21:55:09


In [51]:
#pip install -U textblob

In [55]:
def get_sentiment(text):
    return TextBlob(text).sentiment.polarity

In [56]:
df2['sentiment']=df2['content_c'].apply(get_sentiment)

In [58]:
df2['sentiment_label']=df2['sentiment'].apply(lambda x : 'positive' if x > 0.1 else ('negative' if x < 0.1 else 'neutral'))

In [59]:
df2[['content_c','score','sentiment_label']]

content_c  score  \
0                             i can watch a lot of movies      5   
1       they make you pay for a membership then they t...      1   
2                                                    good      5   
3       i really enjoy netflix but why is netflix conf...      3   
4                           the app doesnt want to update      1   
...                                                   ...    ...   
111150  i really like it there are so many movies and ...      5   
111151     i love netflix i always enjoy my time using it      5   
111152               sound quality is very slow of movies      1   
111153  rate is very expensive bcos we see netflix sun...      1   
111154  this app is awesome for english movies series ...      4   

       sentiment_label  
0             negative  
1             positive  
2             positive  
3             negative  
4             negative  
...                ...  
111150        positive  
111151        positive  
111152        negative  
111153        negative  
111154        positive  

[111155 rows x 3 columns]

In [61]:
neutral_df = df2[df2['sentiment_label'] == 'neutral'][['content_c', 'score', 'sentiment_label']]

In [64]:
neutral_df

content_c  score  \
88                                                    wow      5   
163     how tf do i connect with the same wifi with my...      1   
274                                                   wow      5   
335                         got too greedy for old movies      1   
472                                                   wow      5   
...                                                   ...    ...   
110474  they bring up a lot of old school movies at it...      4   
110790  why do ask for payment so early i updated my p...      1   
110849                       lack of action movies fix it      1   
110983  june  update stopped the app from working comp...      1   
111053                        ease of use simple and fast      5   

       sentiment_label  
88             neutral  
163            neutral  
274            neutral  
335            neutral  
472            neutral  
...                ...  
110474         neutral  
110790         neutral  
110849         neutral  
110983         neutral  
111053         neutral  

[895 rows x 3 columns]

In [71]:
stopwords = set(STOPWORDS)
stopwords.update(['netflix', 'movie', 'show', 'time', 'app', 'series', 'phone'])

In [78]:
negative_words = ','.join(df2[df2['sentiment_label']=='negative']['content_c'])

In [79]:
negative_words

'i can watch a lot of movies,i really enjoy netflix but why is netflix confused in top listing some of movies or series really worst rated movies or series on top after watching ther will be no thrill no entertainment no action no happy ending it will be under  imdb rating,the app doesnt want to update,screen keeps loading on samsung galaxy s,thank you for fixing it,network issues,failed to work,its not even loading properly,سىئ جدا جدا ومسيئ للمجتمع لا انصح بتنزيله ابدا,please improv quality  some date use in this app,in the name of whatever please return the subtitleswhats this,i really used to like the app but since i share an account with my family but dont live with them the app has become entirely useless to me infact the entirety of netflix has become a joke the content is bad the original content is even worse and the companies business practices have become more about trying to milk subscribers for every last cent,maximum time shown errors,wont uninstall though i never use it,

In [81]:
def preprocess_text_data(text):
    tokens = [token for token in text.lower().split() if token.isalnum()] # tokenize text and remove stopwords
    return tokens

texts = [preprocess_text(text) for text in df2[df2['sentiment_label']=='negative']['content_c']]

In [83]:
texts[:5]

['i can watch a lot of movies',
 'i really enjoy netflix but why is netflix confused in top listing some of movies or series really worst rated movies or series on top after watching ther will be no thrill no entertainment no action no happy ending it will be under  imdb rating',
 'the app doesnt want to update',
 'screen keeps loading on samsung galaxy s',
 'thank you for fixing it']

In [84]:
tokenized_texts = [simple_preprocess(text) for text in texts]

In [85]:
tokenized_texts

[['can', 'watch', 'lot', 'of', 'movies'],
 ['really',
  'enjoy',
  'netflix',
  'but',
  'why',
  'is',
  'netflix',
  'confused',
  'in',
  'top',
  'listing',
  'some',
  'of',
  'movies',
  'or',
  'series',
  'really',
  'worst',
  'rated',
  'movies',
  'or',
  'series',
  'on',
  'top',
  'after',
  'watching',
  'ther',
  'will',
  'be',
  'no',
  'thrill',
  'no',
  'entertainment',
  'no',
  'action',
  'no',
  'happy',
  'ending',
  'it',
  'will',
  'be',
  'under',
  'imdb',
  'rating'],
 ['the', 'app', 'doesnt', 'want', 'to', 'update'],
 ['screen', 'keeps', 'loading', 'on', 'samsung', 'galaxy'],
 ['thank', 'you', 'for', 'fixing', 'it'],
 ['network', 'issues'],
 ['failed', 'to', 'work'],
 ['its', 'not', 'even', 'loading', 'properly'],
 ['سىئ', 'جدا', 'جدا', 'ومسيئ', 'للمجتمع', 'لا', 'انصح', 'بتنزيله', 'ابدا'],
 ['please', 'improv', 'quality', 'some', 'date', 'use', 'in', 'this', 'app'],
 ['in',
  'the',
  'name',
  'of',
  'whatever',
  'please',
  'return',
  'the',
  'sub

In [86]:
tokenized_texts = [[word for word in doc if word not in stopwords] for doc in tokenized_texts]

In [88]:
dictionary = corpora.Dictionary(tokenized_texts)

In [89]:
dictionary

In [90]:
corpus = [dictionary.doc2bow(tokens) for tokens in tokenized_texts]

In [92]:
tokenized_texts[0][:5]

['watch', 'lot', 'movies']

In [93]:
lda_model = gensim.models.LdaMulticore(corpus=corpus, id2word=dictionary, num_topics=5, passes=5, workers=2)

In [94]:
topics = lda_model.print_topics(-1)
for idx, topic in topics:
    print(f"Topic {idx}: {topic}")

Topic 0: 0.022*"fix" + 0.020*"screen" + 0.020*"please" + 0.018*"working" + 0.017*"open" + 0.017*"video" + 0.016*"update" + 0.015*"error" + 0.014*"play" + 0.013*"work"
Topic 1: 0.025*"account" + 0.018*"payment" + 0.017*"cant" + 0.014*"service" + 0.011*"use" + 0.011*"please" + 0.011*"money" + 0.011*"subscription" + 0.010*"even" + 0.010*"card"
Topic 2: 0.017*"watch" + 0.016*"please" + 0.013*"watching" + 0.012*"one" + 0.012*"new" + 0.011*"back" + 0.011*"add" + 0.011*"cant" + 0.011*"season" + 0.010*"dont"
Topic 3: 0.036*"cant" + 0.020*"watch" + 0.020*"download" + 0.016*"even" + 0.012*"open" + 0.012*"now" + 0.012*"keeps" + 0.011*"uninstall" + 0.011*"every" + 0.010*"password"
Topic 4: 0.044*"movies" + 0.020*"shows" + 0.017*"watch" + 0.013*"content" + 0.011*"dont" + 0.011*"good" + 0.011*"bad" + 0.007*"money" + 0.007*"quality" + 0.006*"new"
